# Matrix multiplication

In [1]:
import iarray as ia
import numpy as np

Matrix multiplication is a binary operation that produces a matrix from two matrices.
Computing matrix products is a central operation in all computational applications of
linear algebra.

In this tutorial we will see how matrix multiplication works in ironArray while showing how to significantly improve its resource consumption with the use of a simple optimization function. To conclude, we will compare it with NumPy and Zarr+Dask.

First, let us create two chunked, compressed matrices using ironArray. We will choose one of the matrices to be on disk and the other in memory just to show that mixing storage in operands is not a problem:

In [2]:
%load_ext memprofiler

In [3]:
%%mprof_run
ia.set_config(dtype=np.float64)

nrows = 25_000  # number of rows in first matrix
ncols = 100_000   # number of columns in first matrix
ncols2 = 1000     # number of columns in second matrix

shape = (nrows, ncols, ncols2)
amshape = (shape[0], shape[1])
bmshape = (shape[1], shape[2])

filename = "examples/arr-gemm.iarr"
# Remove the file or directory in case it already exists
ia.remove_urlpath(filename)

am = ia.random.normal(amshape, 3, 2, urlpath=filename, fp_mantissa_bits=20)
print(am.info)

w = np.ones(bmshape)
bm = ia.numpy2iarray(w)
print(bm.info)

type   : IArray
shape  : (25000, 100000)
chunks : (512, 4096)
blocks : (32, 512)
cratio : 2.50

type   : IArray
shape  : (100000, 1000)
chunks : (16384, 128)
blocks : (1024, 16)
cratio : 1108.77

memprofiler: used 799.39 MiB RAM (peak of 799.39 MiB) in 55.3778 s, total RAM usage 1005.96 MiB


Unlike numpy, ironArray performs the matrix multiplication using blocks. In this way, instead
of decompressing all the data from the two arrays, we only have to decompress the data needed in each block operation (allowing larger operations with less memory).

Before proceeding, let's evict the just created file from the OS page cache, so as to better assess an actual out of core evaluation from disk.

In [4]:
!vmtouch -e examples/arr-gemm.iarr

           Files: 1226
     Directories: 1
   Evicted Pages: 2009941 (7G)
         Elapsed: 0.5604 seconds


If we use the operator `@` to perform the multiplications in ironArray, all the params of the output array will be those defined in the global configuration.

In [5]:
%%mprof_run iarray::matmul
cm = am @ bm
cm.info

type   : IArray
shape  : (25000, 1000)
chunks : (8192, 256)
blocks : (512, 32)
cratio : 7.92

memprofiler: used 74.73 MiB RAM (peak of 6519.93 MiB) in 62.9115 s, total RAM usage 1081.55 MiB


As said, as the chunk and the block shapes are not defined in the global configuration, they are automatically defined in the output array.

In [6]:
%mprof_plot iarray::matmul -t "Matrix multiplication computation"

Maybe that was not as efficient as we expected, but we will see in the next section how to considerably improve resource consumption with the help of an optimization function.

### Optimization Tips

The latter results were obtained for default chunk and block shapes. But we can get way more performance if we could get optimal values for chunk and block shapes, without having to test different values manually. Indeed, ironArray comes with the handy function `ia.matmul_params` that receives the shapes from the two matrices and returns good guesses for chunk and block shapes so as to compute the matrix multiplication:

In [7]:
# Obtain optimal chunk and block shapes
mparams = ia.matmul_params(amshape, bmshape, itemsize=8)
amchunks, amblocks, bmchunks, bmblocks = mparams

# Remove the on-disk array to create it again
ia.remove_urlpath(filename)

am_opt = ia.random.normal(amshape, 3, 2, chunks=amchunks, blocks=amblocks, urlpath=filename, fp_mantissa_bits=20)
print(am_opt.info)
w = np.ones(bmshape)
bm_opt = ia.numpy2iarray(w, chunks=bmchunks, blocks=bmblocks)
print(bm_opt.info)

type   : IArray
shape  : (25000, 100000)
chunks : (4116, 4116)
blocks : (147, 147)
cratio : 2.86

type   : IArray
shape  : (100000, 1000)
chunks : (4116, 1029)
blocks : (147, 147)
cratio : 788.91



Now, let's compute the multiplication and compare it with the non optimized computation (the one with default chunk and block shapes).

In [8]:
!vmtouch -e examples/arr-gemm.iarr

           Files: 176
     Directories: 1
   Evicted Pages: 2024771 (7G)
         Elapsed: 0.77673 seconds


In [9]:
%%mprof_run iarray::op_matmul
iacm_opt = am_opt @ bm_opt
print(iacm_opt.info)

type   : IArray
shape  : (25000, 1000)
chunks : (4116, 1029)
blocks : (147, 147)
cratio : 41.21

memprofiler: used 51.96 MiB RAM (peak of 51.96 MiB) in 13.1674 s, total RAM usage 1143.05 MiB


In [10]:
%mprof_plot iarray::matmul iarray::op_matmul -t "Matrix computation comparison"

As can be seen, with the chunk and block shapes provided by this function, *much less* memory is consumed (less than 50x) and the execution time has improved *very significantly* too (more than 12x in this case).

Furthermore, we have seen that one way to obtain faster results in ironArray is to favor the speed when computing the multiplication, so let's try it.
To do that, we will need to use the `ia.matmul` function to pass some configuration parameters (see [the documentation](https://ironarray.io/docs/html/reference/autofiles/linalg/iarray.matmul.html#iarray.matmul) for more information) and the btune machinery will have to be activated (the default).

In [11]:
!vmtouch -e examples/arr-gemm.iarr

           Files: 176
     Directories: 1
   Evicted Pages: 2024771 (7G)
         Elapsed: 0.33305 seconds


In [12]:
%%mprof_run iarray::speed_matmul
iacm_speed = ia.matmul(am_opt, bm_opt, favor=ia.Favor.SPEED)
print(iacm_speed.info)

type   : IArray
shape  : (25000, 1000)
chunks : (4116, 1029)
blocks : (147, 147)
cratio : 41.21

memprofiler: used 7.45 MiB RAM (peak of 7.45 MiB) in 13.3202 s, total RAM usage 1150.73 MiB


In [13]:
%mprof_plot iarray::op_matmul iarray::speed_matmul -t "Matrix multiplication computation"

In this case, when favoring speed we do not obtain much benefit. Furthermore, it can be noted that the memory consumption has been reduced to half, but this is due to the fact that the first time the matrix multiplication is computed, ironArray initializes internally some buffers; thus, when computing the second matrix multiplication, those buffers have already been initialized.

Now let's compare with NumPy and Zarr+Dask. We will first set up the arrays, and then compute the matrix multiplication.

In [14]:
npa = am_opt.data
npb = bm_opt.data

In [15]:
%%mprof_run numpy::matmul
npcm = np.matmul(npa, npb)

memprofiler: used 239.29 MiB RAM (peak of 239.29 MiB) in 13.6409 s, total RAM usage 21231.73 MiB


In [16]:
!vmtouch -e examples/arr-gemm.iarr

           Files: 176
     Directories: 1
   Evicted Pages: 2024771 (7G)
         Elapsed: 0.3126 seconds


In [17]:
import zarr
import dask.array as da

zfilename = "examples/arr-gemm.zarr"
ia.remove_urlpath(zfilename)

# Matrix zam goes to disk
zam = zarr.open(zfilename, mode='w', shape=amshape)
am_opt.copyto(zam)
print(zam.info)
dask_a = da.from_zarr(zam)

# Matrix zbm goes to memory
zbm = zarr.create(shape=bmshape)
bm_opt.copyto(zbm)
print(zbm.info)
dask_b = da.from_zarr(zbm)

Type               : zarr.core.Array
Data type          : float64
Shape              : (25000, 100000)
Chunk shape        : (391, 1563)
Order              : C
Read-only          : False
Compressor         : Blosc(cname='lz4', clevel=5, shuffle=SHUFFLE, blocksize=0)
Store type         : zarr.storage.DirectoryStore
No. bytes          : 20000000000 (18.6G)
No. bytes stored   : 8756681815 (8.2G)
Storage ratio      : 2.3
Chunks initialized : 4096/4096

Type               : zarr.core.Array
Data type          : float64
Shape              : (100000, 1000)
Chunk shape        : (3125, 63)
Order              : C
Read-only          : False
Compressor         : Blosc(cname='lz4', clevel=5, shuffle=SHUFFLE, blocksize=0)
Store type         : builtins.dict
No. bytes          : 800000000 (762.9M)
No. bytes stored   : 3246681 (3.1M)
Storage ratio      : 246.4
Chunks initialized : 512/512



In [18]:
!vmtouch -e examples/arr-gemm.zarr

           Files: 4097
     Directories: 1
   Evicted Pages: 2139714 (8G)
         Elapsed: 0.42315 seconds


In [19]:
%%mprof_run dask::matmul
res = da.matmul(dask_a, dask_b)
cshape = (dask_a.shape[0], dask_b.shape[1])
c = zarr.create(shape=cshape)
da.to_zarr(res, c)
print(c.info)

/home/marta/miniconda3/lib/python3.9/site-packages/dask/array/routines.py:385: PerformanceWarning:

Increasing number of chunks by factor of 23



Type               : zarr.core.Array
Data type          : float64
Shape              : (25000, 1000)
Chunk shape        : (1563, 125)
Order              : C
Read-only          : False
Compressor         : Blosc(cname='lz4', clevel=5, shuffle=SHUFFLE, blocksize=0)
Store type         : builtins.dict
No. bytes          : 200000000 (190.7M)
No. bytes stored   : 5512393 (5.3M)
Storage ratio      : 36.3
Chunks initialized : 128/128

memprofiler: used 2076.92 MiB RAM (peak of 2670.71 MiB) in 267.5828 s, total RAM usage 23335.37 MiB


In [20]:
%mprof_plot iarray::op_matmul iarray::matmul numpy::matmul dask::matmul -t "Matrix multiplication computation"

In this summary plot we can see how:

1. ironArray (with default chunk and block shapes) is faster than Zarr+Dask, but way slower than NumPy.
2. ironArray (with optimized chunk and block shapes) uses *much less* memory than any other method.
3. ironArray (with optimized chunk and block shapes) is faster than any other method.

Of course, we could have spent more time optimizing for Zarr optimal values by hand, but the point is that ironArray is providing a function for automatically providing chunks and blocks that are optimized for matrix multiplications; this is something that is not implemented in neither Zarr or Dask.

Finally, the fact that ironArray can be (marginally) faster than NumPy (using MKL) might be due to the fact that MKL is not too well optimized to run on a AMD processors (as is the case here).